In [1]:
import numpy as np
import pandas as pd
from numpy import array
import matplotlib.pyplot as plt

from sklearn.feature_selection import f_classif, mutual_info_classif, SelectFdr

from sklearn.feature_selection import GenericUnivariateSelect
from sklearn.svm import LinearSVC, NuSVC
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier 

from scipy.stats import uniform, randint

import numpy as np
import matplotlib.pyplot as plt
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.datasets import load_digits
from sklearn.model_selection import learning_curve
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import cross_val_score

import xgboost as xgb
from sklearn.metrics import auc, accuracy_score, confusion_matrix, mean_squared_error
from sklearn.model_selection import cross_val_score, GridSearchCV, KFold, RandomizedSearchCV, train_test_split

from warnings import filterwarnings
filterwarnings('ignore')


In [2]:

def plot_learning_curve(estimator, title, X, y, axes=None, ylim=None, cv=None,
                        n_jobs=None, train_sizes=np.linspace(.1, 1.0, 5)):
    """
    Generate 3 plots: the test and training learning curve, the training
    samples vs fit times curve, the fit times vs score curve.

    Parameters
    ----------
    estimator : object type that implements the "fit" and "predict" methods
        An object of that type which is cloned for each validation.

    title : string
        Title for the chart.

    X : array-like, shape (n_samples, n_features)
        Training vector, where n_samples is the number of samples and
        n_features is the number of features.

    y : array-like, shape (n_samples) or (n_samples, n_features), optional
        Target relative to X for classification or regression;
        None for unsupervised learning.

    axes : array of 3 axes, optional (default=None)
        Axes to use for plotting the curves.

    ylim : tuple, shape (ymin, ymax), optional
        Defines minimum and maximum yvalues plotted.

    cv : int, cross-validation generator or an iterable, optional
        Determines the cross-validation splitting strategy.
        Possible inputs for cv are:

          - None, to use the default 5-fold cross-validation,
          - integer, to specify the number of folds.
          - :term:`CV splitter`,
          - An iterable yielding (train, test) splits as arrays of indices.

        For integer/None inputs, if ``y`` is binary or multiclass,
        :class:`StratifiedKFold` used. If the estimator is not a classifier
        or if ``y`` is neither binary nor multiclass, :class:`KFold` is used.

        Refer :ref:`User Guide <cross_validation>` for the various
        cross-validators that can be used here.

    n_jobs : int or None, optional (default=None)
        Number of jobs to run in parallel.
        ``None`` means 1 unless in a :obj:`joblib.parallel_backend` context.
        ``-1`` means using all processors. See :term:`Glossary <n_jobs>`
        for more details.

    train_sizes : array-like, shape (n_ticks,), dtype float or int
        Relative or absolute numbers of training examples that will be used to
        generate the learning curve. If the dtype is float, it is regarded as a
        fraction of the maximum size of the training set (that is determined
        by the selected validation method), i.e. it has to be within (0, 1].
        Otherwise it is interpreted as absolute sizes of the training sets.
        Note that for classification the number of samples usually have to
        be big enough to contain at least one sample from each class.
        (default: np.linspace(0.1, 1.0, 5))
    """
    if axes is None:
        _, axes = plt.subplots(1, 3, figsize=(20, 5))

    axes[0].set_title(title)
    if ylim is not None:
        axes[0].set_ylim(*ylim)
    axes[0].set_xlabel("Training examples")
    axes[0].set_ylabel("Score")

    train_sizes, train_scores, test_scores, fit_times, _ = \
        learning_curve(estimator, X, y, cv=cv, n_jobs=n_jobs,
                       train_sizes=train_sizes,
                       return_times=True)
    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    fit_times_mean = np.mean(fit_times, axis=1)
    fit_times_std = np.std(fit_times, axis=1)

    # Plot learning curve
    axes[0].grid()
    axes[0].fill_between(train_sizes, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.1,
                         color="r")
    axes[0].fill_between(train_sizes, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1,
                         color="g")
    axes[0].plot(train_sizes, train_scores_mean, 'o-', color="r",
                 label="Training score")
    axes[0].plot(train_sizes, test_scores_mean, 'o-', color="g",
                 label="Cross-validation score")
    axes[0].legend(loc="best")

    # Plot n_samples vs fit_times
    axes[1].grid()
    axes[1].plot(train_sizes, fit_times_mean, 'o-')
    axes[1].fill_between(train_sizes, fit_times_mean - fit_times_std,
                         fit_times_mean + fit_times_std, alpha=0.1)
    axes[1].set_xlabel("Training examples")
    axes[1].set_ylabel("fit_times")
    axes[1].set_title("Scalability of the model")

    # Plot fit_time vs score
    axes[2].grid()
    axes[2].plot(fit_times_mean, test_scores_mean, 'o-')
    axes[2].fill_between(fit_times_mean, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1)
    axes[2].set_xlabel("fit_times")
    axes[2].set_ylabel("Score")
    axes[2].set_title("Performance of the model")

    return plt

In [3]:
def hyper_opt_procedure(model_object,params,cv,perf_df,X,y):


  model = model_object()

  # Initial Model Fit with stock hyper_params

  init_score = np.mean(cross_val_score(model,X,y,cv=cv))

  perf_df = perf_df.append({'Model Iteration': 'Stock Params',
                              'Score':init_score}, ignore_index=True)

  print('Initial Model with Stock Params Score : {}'.format(init_score))

  # Random Search Cross Validation


  search_model = RandomizedSearchCV(model,
                                         param_distributions=params,
                                         random_state=42, 
                                         n_iter=300, 
                                         cv=cv, 
                                         verbose=1, 
                                         n_jobs=1, 
                                         return_train_score=True)

  search_model.fit(X,y)

  best_search_model = search_model.best_estimator_

  best_search_model_score = search_model.best_score_

  perf_df = perf_df.append({'Model Iteration': 'Random HP Search Best Model',
                      'Score':best_search_model_score}, ignore_index=True)

  rd_score_improv = ((best_search_model_score - init_score)/init_score) * 100

  print('Random HP Search Best Model Score : {}'.format(best_search_model_score))

  print('Improvement of {}% relative to the initial model'.format(rd_score_improv))
  
  


  return model, best_search_model
   



class hyper_model:
    
    def __init__(self,model_name,validation_approach,X,y):
        
        self.model_name = model_name
        self.X = X
        self.y = y
        self.validation_approach= validation_approach
        self.best_model = None
        self.best_params = None
        self.all_models_perf = pd.DataFrame(None,columns=['Model Iteration','Score'])
        self.stock_model = None
        self.rd_model = None


    def fit(self):


      if self.validation_approach == 'leave-one-run-out':

        cv = KFold(n_splits=8, shuffle=False)

      elif self.validation_approach == 'leave-one-run-out-shuffled':

        cv = KFold(n_splits=8, shuffle=True, random_state=42)

      elif self.validation_approach == 'leave-one-task-out':

        cv = KFold(n_splits=4, shuffle=False)

      elif self.validation_approach == 'leave-one-task-out-shuffled':

        cv = KFold(n_splits=4, shuffle=True, random_state=42)    


 
        
        # Linear SVM

      if self.model_name == 'linear_svm':

        params = {'C': [0.1, 1, 10, 100, 1000]} 

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=LinearSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

         

      # Non Linear SVM


      elif self.model_name == 'non_linear_svm':

        params = {'nu': [0.01, 0.3, 0.5, 0.7, 1],  
                        'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
                        'kernel': ['rbf','poly','sigmoid']
                       }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=NuSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

          
      # Random Forest Classifier


      elif self.model_name == 'random_forest_classifier':


        params = {'bootstrap': [True],
                    'max_depth': [60],
                    'max_features': ['auto'],
                    'min_samples_leaf': [4],
                    'min_samples_split': [2, 5],
                    'n_estimators': [1000]
                   }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=RandomForestClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)
          



      # XG Boost Classifier


      elif self.model_name == 'xg_boost':

        params = {
              "colsample_bytree": uniform(0.7, 0.3),
              "gamma": uniform(0, 0.5),
              "learning_rate": uniform(0.03, 0.3), 
              "max_depth": randint(2, 6), 
              "n_estimators": randint(100, 150),
              "subsample": uniform(0.6, 0.4)
              }

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=xgb.XGBClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)  

                
                

In [4]:
X = np.load('../../data/X_pref_lss_shift_quadratic_vmpfc.npy')

In [5]:
X.shape

(480, 87)

In [6]:
y = np.load('../../data/y_pref_lss_shift_quadratic_vmpfc.npy')

In [7]:
y.shape

(480, 1)

## Features Selection

### Filter
No FS needed

### Data Preparation

In [8]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.10, random_state=42)

## Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [9]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [10]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4166666666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5354166666666667
Improvement of 28.499999999999993% relative to the initial model


[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.7s finished


In [11]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [12]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [13]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.3       ])

In [14]:
mean_score

0.43333333333333335

In [15]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [16]:
scores

array([0.24166667, 0.325     , 0.30833333, 0.23333333])

In [17]:
mean_score

0.27708333333333335

In [18]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [19]:
scores

array([0.61666667, 0.48333333, 0.35      , 0.36666667, 0.5       ,
       0.51666667, 0.73333333, 0.73333333])

In [20]:
mean_score

0.5375

In [21]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [22]:
scores

array([0.13333333, 0.2       , 0.28333333, 0.25      , 0.25      ,
       0.16666667, 0.25      , 0.15      ])

In [23]:
mean_score

0.21041666666666667

In [24]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [25]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [26]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.2791666666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.41875
Improvement of 50.0% relative to the initial model


[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.7s finished


In [27]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [28]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [29]:
scores

array([0.55833333, 0.36666667, 0.51666667, 0.35833333])

In [30]:
mean_score

0.45000000000000007

In [31]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [32]:
scores

array([0.25      , 0.30833333, 0.275     , 0.24166667])

In [33]:
mean_score

0.26875

In [34]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [35]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.6       , 0.73333333])

In [36]:
mean_score

0.5249999999999999

In [37]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [38]:
scores

array([0.15      , 0.18333333, 0.28333333, 0.25      , 0.26666667,
       0.16666667, 0.25      , 0.15      ])

In [39]:
mean_score

0.21250000000000002

In [40]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [41]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [42]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.5395833333333333
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 1.9305019305019444% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    1.9s finished


In [43]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [44]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [45]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.28333333])

In [46]:
mean_score

0.4291666666666667

In [47]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [48]:
scores

array([0.25      , 0.33333333, 0.275     , 0.23333333])

In [49]:
mean_score

0.27291666666666664

In [50]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [51]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.76666667, 0.73333333])

In [52]:
mean_score

0.5458333333333334

In [53]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [54]:
scores

array([0.18333333, 0.2       , 0.28333333, 0.26666667, 0.28333333,
       0.16666667, 0.3       , 0.13333333])

In [55]:
mean_score

0.22708333333333333

In [56]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [57]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [58]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.2125
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.42291666666666666
Improvement of 99.01960784313727% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    1.9s finished


In [59]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [60]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [61]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.225     ])

In [62]:
mean_score

0.41458333333333336

In [63]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [64]:
scores

array([0.25      , 0.33333333, 0.29166667, 0.25833333])

In [65]:
mean_score

0.2833333333333333

In [66]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [67]:
scores

array([0.58333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.76666667, 0.68333333])

In [68]:
mean_score

0.5333333333333333

In [69]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [70]:
scores

array([0.15      , 0.18333333, 0.26666667, 0.25      , 0.3       ,
       0.16666667, 0.23333333, 0.11666667])

In [71]:
mean_score

0.20833333333333331

In [72]:
# other metrics + graphs




### Hyper_optimized model

#### *leave-one-task-out* cross validation

##### Training

In [73]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [74]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.44166666666666665
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.50625
Improvement of 14.622641509433961% relative to the initial model


[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.7s finished


In [75]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [76]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [77]:
scores

array([0.46666667, 0.43333333, 0.44166667, 0.45833333])

In [78]:
mean_score

0.45

In [79]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [80]:
scores

array([0.325     , 0.54166667, 0.43333333, 0.39166667])

In [81]:
mean_score

0.42291666666666666

In [82]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [83]:
scores

array([0.5       , 0.5       , 0.38333333, 0.43333333, 0.53333333,
       0.5       , 0.53333333, 0.45      ])

In [84]:
mean_score

0.47916666666666663

In [85]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [86]:
scores

array([0.53333333, 0.5       , 0.51666667, 0.38333333, 0.48333333,
       0.45      , 0.43333333, 0.38333333])

In [87]:
mean_score

0.4604166666666667

In [88]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [89]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [90]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.28125
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.41041666666666665
Improvement of 45.92592592592592% relative to the initial model


[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.7s finished


In [91]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [92]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [93]:
scores

array([0.49166667, 0.43333333, 0.45833333, 0.55      ])

In [94]:
mean_score

0.48333333333333334

In [95]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [96]:
scores

array([0.35833333, 0.375     , 0.39166667, 0.31666667])

In [97]:
mean_score

0.36041666666666666

In [98]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [99]:
scores

array([0.51666667, 0.51666667, 0.53333333, 0.45      , 0.48333333,
       0.48333333, 0.55      , 0.51666667])

In [100]:
mean_score

0.5062500000000001

In [101]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [102]:
scores

array([0.53333333, 0.41666667, 0.43333333, 0.43333333, 0.36666667,
       0.45      , 0.46666667, 0.43333333])

In [103]:
mean_score

0.44166666666666665

In [104]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [105]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [106]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.5416666666666667
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 1.5384615384615328% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    1.9s finished


In [107]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [108]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [109]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [110]:
mean_score

0.4166666666666667

In [111]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [112]:
scores

array([0.25      , 0.33333333, 0.28333333, 0.25      ])

In [113]:
mean_score

0.2791666666666667

In [114]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [115]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [116]:
mean_score

0.55

In [117]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [118]:
scores

array([0.21666667, 0.23333333, 0.28333333, 0.23333333, 0.3       ,
       0.2       , 0.26666667, 0.18333333])

In [119]:
mean_score

0.23958333333333331

In [120]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [121]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [122]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.2125
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.43333333333333335
Improvement of 103.921568627451% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    2.0s finished


In [123]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [124]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [125]:
scores

array([0.45      , 0.43333333, 0.51666667, 0.48333333])

In [126]:
mean_score

0.4708333333333333

In [127]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [128]:
scores

array([0.41666667, 0.41666667, 0.40833333, 0.45      ])

In [129]:
mean_score

0.42291666666666666

In [130]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [131]:
scores

array([0.5       , 0.51666667, 0.46666667, 0.48333333, 0.5       ,
       0.5       , 0.55      , 0.55      ])

In [132]:
mean_score

0.5083333333333333

In [133]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [134]:
scores

array([0.35      , 0.41666667, 0.51666667, 0.45      , 0.43333333,
       0.35      , 0.36666667, 0.41666667])

In [135]:
mean_score

0.4125

In [136]:
# other metrics + graphs




## Non Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [137]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [138]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.48541666666666666
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5729166666666667
Improvement of 18.02575107296139% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:    3.9s finished


In [139]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [140]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [141]:
scores

array([0.48333333, 0.525     , 0.45      , 0.48333333])

In [142]:
mean_score

0.48541666666666666

In [143]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [144]:
scores

array([0.43333333, 0.475     , 0.475     , 0.48333333])

In [145]:
mean_score

0.4666666666666667

In [146]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [147]:
scores

array([0.43333333, 0.46666667, 0.55      , 0.5       , 0.45      ,
       0.46666667, 0.5       , 0.55      ])

In [148]:
mean_score

0.48958333333333337

In [149]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [150]:
scores

array([0.45      , 0.51666667, 0.45      , 0.45      , 0.53333333,
       0.5       , 0.5       , 0.38333333])

In [151]:
mean_score

0.47291666666666665

In [152]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [153]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [154]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.4666666666666667
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5562499999999999
Improvement of 19.19642857142855% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:    3.9s finished


In [155]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [156]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [157]:
scores

array([0.48333333, 0.525     , 0.45      , 0.48333333])

In [158]:
mean_score

0.48541666666666666

In [159]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [160]:
scores

array([0.43333333, 0.475     , 0.475     , 0.48333333])

In [161]:
mean_score

0.4666666666666667

In [162]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [163]:
scores

array([0.43333333, 0.46666667, 0.55      , 0.5       , 0.45      ,
       0.46666667, 0.5       , 0.55      ])

In [164]:
mean_score

0.48958333333333337

In [165]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [166]:
scores

array([0.45      , 0.51666667, 0.45      , 0.45      , 0.53333333,
       0.5       , 0.5       , 0.38333333])

In [167]:
mean_score

0.47291666666666665

In [168]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [169]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [170]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.48958333333333337
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5625
Improvement of 14.893617021276587% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:    9.9s finished


In [171]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [172]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [173]:
scores

array([0.48333333, 0.525     , 0.45      , 0.48333333])

In [174]:
mean_score

0.48541666666666666

In [175]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [176]:
scores

array([0.43333333, 0.475     , 0.475     , 0.48333333])

In [177]:
mean_score

0.4666666666666667

In [178]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [179]:
scores

array([0.43333333, 0.46666667, 0.55      , 0.5       , 0.45      ,
       0.46666667, 0.5       , 0.55      ])

In [180]:
mean_score

0.48958333333333337

In [181]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [182]:
scores

array([0.45      , 0.51666667, 0.45      , 0.45      , 0.53333333,
       0.5       , 0.5       , 0.38333333])

In [183]:
mean_score

0.47291666666666665

In [184]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [185]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [186]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.47291666666666665
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5541666666666667
Improvement of 17.180616740088116% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   10.0s finished


In [187]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [188]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [189]:
scores

array([0.48333333, 0.525     , 0.45      , 0.48333333])

In [190]:
mean_score

0.48541666666666666

In [191]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [192]:
scores

array([0.43333333, 0.475     , 0.475     , 0.48333333])

In [193]:
mean_score

0.4666666666666667

In [194]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [195]:
scores

array([0.43333333, 0.46666667, 0.55      , 0.5       , 0.45      ,
       0.46666667, 0.5       , 0.55      ])

In [196]:
mean_score

0.48958333333333337

In [197]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [198]:
scores

array([0.45      , 0.51666667, 0.45      , 0.45      , 0.53333333,
       0.5       , 0.5       , 0.38333333])

In [199]:
mean_score

0.47291666666666665

In [200]:
# other metrics + graphs




### Hyper_optimized model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [201]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [202]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.48541666666666666
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5729166666666667
Improvement of 18.02575107296139% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:    3.9s finished


In [203]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [204]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [205]:
scores

array([0.51666667, 0.55833333, 0.51666667, 0.7       ])

In [206]:
mean_score

0.5729166666666667

In [207]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [208]:
scores

array([0.54166667, 0.49166667, 0.44166667, 0.45833333])

In [209]:
mean_score

0.4833333333333333

In [210]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [211]:
scores

array([0.63333333, 0.5       , 0.43333333, 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [212]:
mean_score

0.5625

In [213]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [214]:
scores

array([0.46666667, 0.41666667, 0.5       , 0.46666667, 0.5       ,
       0.43333333, 0.45      , 0.45      ])

In [215]:
mean_score

0.4604166666666667

In [216]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [217]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [218]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.4666666666666667
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5562499999999999
Improvement of 19.19642857142855% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:    3.9s finished


In [219]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [220]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [221]:
scores

array([0.53333333, 0.36666667, 0.50833333, 0.33333333])

In [222]:
mean_score

0.4354166666666666

In [225]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [226]:
scores

array([0.50833333, 0.53333333, 0.63333333, 0.55      ])

In [227]:
mean_score

0.5562499999999999

In [228]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [229]:
scores

array([0.6       , 0.5       , 0.43333333, 0.41666667, 0.5       ,
       0.51666667, 0.61666667, 0.68333333])

In [230]:
mean_score

0.5333333333333333

In [231]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [232]:
scores

array([0.48333333, 0.51666667, 0.53333333, 0.56666667, 0.68333333,
       0.58333333, 0.53333333, 0.53333333])

In [233]:
mean_score

0.5541666666666667

In [234]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [235]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [236]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.48958333333333337
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5625
Improvement of 14.893617021276587% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:    9.9s finished


In [237]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [238]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [239]:
scores

array([0.51666667, 0.55833333, 0.51666667, 0.7       ])

In [240]:
mean_score

0.5729166666666667

In [241]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [242]:
scores

array([0.54166667, 0.49166667, 0.44166667, 0.45833333])

In [243]:
mean_score

0.4833333333333333

In [244]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [245]:
scores

array([0.63333333, 0.5       , 0.43333333, 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [246]:
mean_score

0.5625

In [247]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [248]:
scores

array([0.46666667, 0.41666667, 0.5       , 0.46666667, 0.5       ,
       0.43333333, 0.45      , 0.45      ])

In [249]:
mean_score

0.4604166666666667

In [250]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [251]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [252]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.47291666666666665
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5541666666666667
Improvement of 17.180616740088116% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   10.1s finished


In [253]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [254]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [255]:
scores

array([0.53333333, 0.36666667, 0.50833333, 0.33333333])

In [256]:
mean_score

0.4354166666666666

In [257]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [258]:
scores

array([0.50833333, 0.53333333, 0.63333333, 0.55      ])

In [259]:
mean_score

0.5562499999999999

In [260]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [261]:
scores

array([0.6       , 0.5       , 0.43333333, 0.41666667, 0.5       ,
       0.51666667, 0.61666667, 0.68333333])

In [262]:
mean_score

0.5333333333333333

In [263]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [264]:
scores

array([0.48333333, 0.51666667, 0.53333333, 0.56666667, 0.68333333,
       0.58333333, 0.53333333, 0.53333333])

In [265]:
mean_score

0.5541666666666667

In [266]:
# other metrics + graphs




## Random Forest Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [267]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [268]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.4041666666666667
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   13.2s finished


Random HP Search Best Model Score : 0.42291666666666666
Improvement of 4.6391752577319565% relative to the initial model


In [269]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [270]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [271]:
scores

array([0.43333333, 0.36666667, 0.45      , 0.36666667])

In [272]:
mean_score

0.4041666666666667

In [273]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [274]:
scores

array([0.39166667, 0.44166667, 0.49166667, 0.46666667])

In [275]:
mean_score

0.44791666666666663

In [276]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [277]:
scores

array([0.46666667, 0.45      , 0.41666667, 0.5       , 0.43333333,
       0.55      , 0.4       , 0.55      ])

In [278]:
mean_score

0.4708333333333334

In [279]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [280]:
scores

array([0.41666667, 0.43333333, 0.46666667, 0.45      , 0.43333333,
       0.41666667, 0.41666667, 0.43333333])

In [281]:
mean_score

0.43333333333333335

In [282]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [283]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [284]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.45
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   13.2s finished


Random HP Search Best Model Score : 0.4541666666666667
Improvement of 0.9259259259259349% relative to the initial model


In [285]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [286]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [287]:
scores

array([0.45833333, 0.40833333, 0.425     , 0.375     ])

In [288]:
mean_score

0.4166666666666667

In [289]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [290]:
scores

array([0.39166667, 0.45833333, 0.5       , 0.425     ])

In [291]:
mean_score

0.44375000000000003

In [292]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [293]:
scores

array([0.46666667, 0.38333333, 0.45      , 0.4       , 0.45      ,
       0.43333333, 0.43333333, 0.53333333])

In [294]:
mean_score

0.44375000000000003

In [295]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [296]:
scores

array([0.33333333, 0.45      , 0.46666667, 0.43333333, 0.33333333,
       0.4       , 0.46666667, 0.45      ])

In [297]:
mean_score

0.4166666666666667

In [298]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [299]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [300]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.45625000000000004
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:   30.2s finished


Random HP Search Best Model Score : 0.46041666666666664
Improvement of 0.9132420091324046% relative to the initial model


In [301]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [302]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [303]:
scores

array([0.46666667, 0.38333333, 0.44166667, 0.34166667])

In [304]:
mean_score

0.4083333333333333

In [305]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [306]:
scores

array([0.4       , 0.49166667, 0.46666667, 0.425     ])

In [307]:
mean_score

0.44583333333333336

In [308]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [309]:
scores

array([0.55      , 0.5       , 0.46666667, 0.38333333, 0.45      ,
       0.46666667, 0.33333333, 0.48333333])

In [310]:
mean_score

0.4541666666666667

In [311]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [312]:
scores

array([0.45      , 0.48333333, 0.36666667, 0.45      , 0.41666667,
       0.45      , 0.5       , 0.5       ])

In [313]:
mean_score

0.45208333333333334

In [314]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [315]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [316]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.4708333333333333
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:   29.2s finished


Random HP Search Best Model Score : 0.45416666666666666
Improvement of -3.539823008849557% relative to the initial model


In [317]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [318]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [319]:
scores

array([0.45833333, 0.375     , 0.45833333, 0.39166667])

In [320]:
mean_score

0.4208333333333333

In [321]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [322]:
scores

array([0.36666667, 0.48333333, 0.5       , 0.425     ])

In [323]:
mean_score

0.44375000000000003

In [324]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [325]:
scores

array([0.55      , 0.5       , 0.45      , 0.45      , 0.46666667,
       0.48333333, 0.33333333, 0.56666667])

In [326]:
mean_score

0.475

In [327]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [328]:
scores

array([0.41666667, 0.46666667, 0.43333333, 0.43333333, 0.4       ,
       0.41666667, 0.4       , 0.36666667])

In [329]:
mean_score

0.41666666666666663

In [330]:
# other metrics + graphs




### Hyper_optimized Model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [331]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [332]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.42291666666666666
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   13.1s finished


Random HP Search Best Model Score : 0.4125
Improvement of -2.4630541871921223% relative to the initial model


In [333]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [334]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [335]:
scores

array([0.45      , 0.375     , 0.45833333, 0.375     ])

In [336]:
mean_score

0.4145833333333333

In [337]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [338]:
scores

array([0.39166667, 0.44166667, 0.51666667, 0.44166667])

In [339]:
mean_score

0.4479166666666667

In [340]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [341]:
scores

array([0.45      , 0.43333333, 0.38333333, 0.35      , 0.51666667,
       0.5       , 0.48333333, 0.56666667])

In [342]:
mean_score

0.46041666666666664

In [343]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [344]:
scores

array([0.38333333, 0.5       , 0.41666667, 0.46666667, 0.43333333,
       0.51666667, 0.45      , 0.45      ])

In [345]:
mean_score

0.45208333333333334

In [346]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [347]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [348]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.43124999999999997
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   13.2s finished


Random HP Search Best Model Score : 0.46249999999999997
Improvement of 7.246376811594203% relative to the initial model


In [349]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [350]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [351]:
scores

array([0.45833333, 0.36666667, 0.49166667, 0.34166667])

In [352]:
mean_score

0.4145833333333333

In [353]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [354]:
scores

array([0.38333333, 0.45      , 0.50833333, 0.45      ])

In [355]:
mean_score

0.4479166666666667

In [356]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [357]:
scores

array([0.5       , 0.45      , 0.38333333, 0.38333333, 0.53333333,
       0.51666667, 0.38333333, 0.58333333])

In [358]:
mean_score

0.4666666666666667

In [359]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [360]:
scores

array([0.4       , 0.43333333, 0.43333333, 0.43333333, 0.4       ,
       0.56666667, 0.46666667, 0.43333333])

In [361]:
mean_score

0.44583333333333336

In [362]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [363]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [364]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.45833333333333337
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:   30.1s finished


Random HP Search Best Model Score : 0.4625
Improvement of 0.9090909090909057% relative to the initial model


In [365]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [366]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [367]:
scores

array([0.45      , 0.36666667, 0.5       , 0.35833333])

In [368]:
mean_score

0.41875

In [369]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [370]:
scores

array([0.4       , 0.44166667, 0.5       , 0.43333333])

In [371]:
mean_score

0.44375000000000003

In [372]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [373]:
scores

array([0.46666667, 0.43333333, 0.36666667, 0.38333333, 0.5       ,
       0.46666667, 0.43333333, 0.58333333])

In [374]:
mean_score

0.45416666666666666

In [375]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [376]:
scores

array([0.4       , 0.45      , 0.48333333, 0.43333333, 0.41666667,
       0.55      , 0.43333333, 0.46666667])

In [377]:
mean_score

0.4541666666666667

In [378]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [379]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [380]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.45625000000000004
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:   29.7s finished


Random HP Search Best Model Score : 0.45833333333333337
Improvement of 0.45662100456620835% relative to the initial model


In [381]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [382]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [383]:
scores

array([0.45      , 0.375     , 0.5       , 0.35833333])

In [384]:
mean_score

0.42083333333333334

In [385]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [386]:
scores

array([0.39166667, 0.425     , 0.5       , 0.48333333])

In [387]:
mean_score

0.45

In [388]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [389]:
scores

array([0.51666667, 0.41666667, 0.36666667, 0.36666667, 0.51666667,
       0.48333333, 0.46666667, 0.56666667])

In [390]:
mean_score

0.46249999999999997

In [391]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [392]:
scores

array([0.41666667, 0.46666667, 0.43333333, 0.41666667, 0.41666667,
       0.56666667, 0.46666667, 0.45      ])

In [393]:
mean_score

0.4541666666666667

In [394]:
# other metrics + graphs




## XGBoost Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [395]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [396]:
hm_xgb_to.fit()

[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.



[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_re

[07:52:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:52:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:52:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[07:53:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:53:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:53:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:53:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:54:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  1.6min finished


In [397]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [398]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [399]:
scores

array([0.45      , 0.41666667, 0.5       , 0.38333333])

In [400]:
mean_score

0.4375

In [401]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [402]:
scores

array([0.375     , 0.425     , 0.45      , 0.36666667])

In [403]:
mean_score

0.4041666666666667

In [404]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:54:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [405]:
scores

array([0.43333333, 0.36666667, 0.45      , 0.38333333, 0.53333333,
       0.45      , 0.48333333, 0.51666667])

In [406]:
mean_score

0.45208333333333334

In [407]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [408]:
scores

array([0.46666667, 0.41666667, 0.46666667, 0.41666667, 0.4       ,
       0.43333333, 0.38333333, 0.45      ])

In [409]:
mean_score

0.4291666666666667

In [410]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [411]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [412]:
hm_xgb_tos.fit()

[07:54:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[07:54:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:54:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:54:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:54:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[07:55:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:55:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:55:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  1.7min finished


[07:55:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.4666666666666667
Improvement of 15.463917525773196% relative to the initial model


In [413]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [414]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[07:55:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [415]:
scores

array([0.45      , 0.41666667, 0.5       , 0.38333333])

In [416]:
mean_score

0.4375

In [417]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [418]:
scores

array([0.375     , 0.425     , 0.45      , 0.36666667])

In [419]:
mean_score

0.4041666666666667

In [420]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [421]:
scores

array([0.43333333, 0.36666667, 0.45      , 0.38333333, 0.53333333,
       0.45      , 0.48333333, 0.51666667])

In [422]:
mean_score

0.45208333333333334

In [423]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[07:55:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [424]:
scores

array([0.46666667, 0.41666667, 0.46666667, 0.41666667, 0.4       ,
       0.43333333, 0.38333333, 0.45      ])

In [425]:
mean_score

0.4291666666666667

In [426]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [427]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [428]:
hm_xgb_ro.fit()

[07:55:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.



[07:55:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_re

[07:55:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:55:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:55:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:00:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:00:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:00:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:00:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:01:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:01:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:01:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed:  5.4min finished


In [429]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [430]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [431]:
scores

array([0.45      , 0.41666667, 0.5       , 0.38333333])

In [432]:
mean_score

0.4375

In [433]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [434]:
scores

array([0.375     , 0.425     , 0.45      , 0.36666667])

In [435]:
mean_score

0.4041666666666667

In [436]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:01:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [437]:
scores

array([0.43333333, 0.36666667, 0.45      , 0.38333333, 0.53333333,
       0.45      , 0.48333333, 0.51666667])

In [438]:
mean_score

0.45208333333333334

In [439]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:01:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [440]:
scores

array([0.46666667, 0.41666667, 0.46666667, 0.41666667, 0.4       ,
       0.43333333, 0.38333333, 0.45      ])

In [441]:
mean_score

0.4291666666666667

In [442]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [443]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [444]:
hm_xgb_ros.fit()

[08:01:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:01:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:01:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:01:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:01:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:13:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 12.2min finished


Random HP Search Best Model Score : 0.46875
Improvement of 9.22330097087378% relative to the initial model


In [445]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [446]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:13:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [447]:
scores

array([0.45      , 0.41666667, 0.5       , 0.38333333])

In [448]:
mean_score

0.4375

In [449]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:13:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [450]:
scores

array([0.375     , 0.425     , 0.45      , 0.36666667])

In [451]:
mean_score

0.4041666666666667

In [452]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:13:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [453]:
scores

array([0.43333333, 0.36666667, 0.45      , 0.38333333, 0.53333333,
       0.45      , 0.48333333, 0.51666667])

In [454]:
mean_score

0.45208333333333334

In [455]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:13:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [456]:
scores

array([0.46666667, 0.41666667, 0.46666667, 0.41666667, 0.4       ,
       0.43333333, 0.38333333, 0.45      ])

In [457]:
mean_score

0.4291666666666667

In [458]:
# other metrics + graphs




### Hyper_optimized model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [459]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [460]:
hm_xgb_to.fit()

[08:13:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:13:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:25:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:25:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:25:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:25:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:26:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:26:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 13.0min finished


[08:26:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.48333333333333334
Improvement of 10.476190476190476% relative to the initial model


In [461]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [462]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:26:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [463]:
scores

array([0.51666667, 0.46666667, 0.50833333, 0.44166667])

In [464]:
mean_score

0.48333333333333334

In [465]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:27:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [466]:
scores

array([0.34166667, 0.45833333, 0.44166667, 0.44166667])

In [467]:
mean_score

0.42083333333333334

In [468]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:27:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [469]:
scores

array([0.51666667, 0.48333333, 0.6       , 0.41666667, 0.45      ,
       0.46666667, 0.46666667, 0.45      ])

In [470]:
mean_score

0.48125

In [471]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:28:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:28:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:28:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:28:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [472]:
scores

array([0.46666667, 0.46666667, 0.45      , 0.5       , 0.33333333,
       0.55      , 0.43333333, 0.43333333])

In [473]:
mean_score

0.45416666666666666

In [474]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [475]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [476]:
hm_xgb_tos.fit()

[08:29:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:29:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:29:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:29:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:30:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:30:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:30:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:30:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:43:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:43:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:43:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:43:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:44:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:44:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:44:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:44:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:45:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:45:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:45:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:45:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 16.4min finished


[08:45:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.4666666666666667
Improvement of 15.463917525773196% relative to the initial model


In [477]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [478]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:45:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:45:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:45:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [479]:
scores

array([0.51666667, 0.45833333, 0.45      , 0.44166667])

In [480]:
mean_score

0.4666666666666667

In [481]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:46:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [482]:
scores

array([0.45833333, 0.49166667, 0.425     , 0.49166667])

In [483]:
mean_score

0.4666666666666667

In [484]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:46:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [485]:
scores

array([0.45      , 0.51666667, 0.45      , 0.43333333, 0.5       ,
       0.5       , 0.51666667, 0.48333333])

In [486]:
mean_score

0.48125

In [487]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:47:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [488]:
scores

array([0.38333333, 0.36666667, 0.5       , 0.38333333, 0.31666667,
       0.5       , 0.36666667, 0.48333333])

In [489]:
mean_score

0.4125

In [490]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [491]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [492]:
hm_xgb_ro.fit()

[08:48:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:48:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:49:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:49:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:50:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[10:09:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:09:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:09:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:09:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:10:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:10:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:10:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:10:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:11:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:11:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:11:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:11:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 82.7min finished


[10:11:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.53125
Improvement of 17.51152073732719% relative to the initial model


In [493]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [494]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[10:12:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [495]:
scores

array([0.45833333, 0.45      , 0.475     , 0.41666667])

In [496]:
mean_score

0.45

In [497]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:12:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:12:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [498]:
scores

array([0.34166667, 0.45833333, 0.44166667, 0.40833333])

In [499]:
mean_score

0.4125

In [500]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:13:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [501]:
scores

array([0.45      , 0.51666667, 0.58333333, 0.48333333, 0.6       ,
       0.55      , 0.53333333, 0.53333333])

In [502]:
mean_score

0.53125

In [503]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:13:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:13:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [504]:
scores

array([0.45      , 0.48333333, 0.43333333, 0.45      , 0.4       ,
       0.46666667, 0.36666667, 0.5       ])

In [505]:
mean_score

0.44375

In [506]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [507]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [508]:
hm_xgb_ros.fit()

[10:14:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:14:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:14:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:14:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[10:15:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:15:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:15:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:15:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:16:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:16:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:16:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:16:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:17:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:17:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:17:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:17:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[11:40:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:40:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:40:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:41:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 86.6min finished


[11:41:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.46875
Improvement of 9.22330097087378% relative to the initial model


In [509]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [510]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



The history saving thread hit an unexpected error (OperationalError('database is locked')).History will not be written to the database.
[11:41:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Expl

In [511]:
scores

array([0.48333333, 0.43333333, 0.45      , 0.425     ])

In [512]:
mean_score

0.4479166666666667

In [513]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:41:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [514]:
scores

array([0.41666667, 0.43333333, 0.41666667, 0.44166667])

In [515]:
mean_score

0.42708333333333337

In [516]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:41:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:41:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [517]:
scores

array([0.4       , 0.53333333, 0.48333333, 0.4       , 0.51666667,
       0.45      , 0.51666667, 0.5       ])

In [518]:
mean_score

0.475

In [519]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:41:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:42:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:42:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:42:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [520]:
scores

array([0.5       , 0.5       , 0.41666667, 0.41666667, 0.41666667,
       0.5       , 0.53333333, 0.46666667])

In [521]:
mean_score

0.46875

In [522]:
# other metrics + graphs


